# Extract Regulatory ID

In [1]:
import os

file_list = []

def list_files_and_subdirectories(directory):
    for root, dirs, files in os.walk(directory):
        print("Current directory:", root)
        print("Subdirectories:", dirs)
        print("Files:", files)
        print()
        
        if len(dirs) == 0 and len(files) > 0:
            for f in files:
                file_list.append(f'{root}/{f}')

list_files_and_subdirectories('new_1_text_files')

Current directory: new_1_text_files
Subdirectories: ['perda', 'putusan', 'bn', 'ln', 'lain-lain']
Files: []

Current directory: new_1_text_files/perda
Subdirectories: ['1994', '1982', '1992', '2015', '2010', '2003', '1979', '2019', '2012', '1998', '1989', '1996', '1976', '2008', '2013', '1984', '2002', '1991', '1995', '1986', '1983', '2006', '2011', '2004', '1977', '1999', '2009', '1985', '1997', '1990', '2014', '2007', '2018', '2000', '1987', '1980', '1993', '2017', '1981', '2001', '2016', '2005', '1988']
Files: []

Current directory: new_1_text_files/perda/1994
Subdirectories: []
Files: ['perda_kabupaten_bantul_nomor_1_tahun_1994_11e4f455eafd9d9e96f8303831303537.txt', 'perda_kabupaten_bantul_nomor_13_tahun_1994_11e4f455ce0fe070b477303831303039.txt', 'perda_kabupaten_bantul_nomor_5_tahun_1994_11e4f455bc59cfd09767303830393339.txt', 'perda_kabupaten_bantul_nomor_11_tahun_1994_11e4f455e25cf3ec9c34303831303433.txt', 'perda_kabupaten_bantul_nomor_4_tahun_1994_11e4f455c5bbe504856d3038303935

In [2]:
file_list

['new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_1_tahun_1994_11e4f455eafd9d9e96f8303831303537.txt',
 'new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_13_tahun_1994_11e4f455ce0fe070b477303831303039.txt',
 'new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_5_tahun_1994_11e4f455bc59cfd09767303830393339.txt',
 'new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_11_tahun_1994_11e4f455e25cf3ec9c34303831303433.txt',
 'new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_4_tahun_1994_11e4f455c5bbe504856d303830393535.txt',
 'new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_6_tahun_1994_11e4f455b2fb1fb69ab7303830393234.txt',
 'new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_7_tahun_1994_11e4f455aade1374a598303830393130.txt',
 'new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_8_tahun_1994_11e4f4559f0d8066b1aa303830383530.txt',
 'new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_12_tahun_1994_11e4f455d91c1268a69d303831303237.txt'

In [3]:
print(len(file_list))

30478


In [4]:
import json
import os
import re

import pandas

pandas.set_option('display.max_colwidth', 300)
pandas.set_option('display.width', None)


def get_title(texts, is_doc=True):
    try:
        if is_doc:
            filtered_text = re.search(r'((PERUBAHAN[\s\n]+(PERTAMA|KE(DUA|TIGA|EMPAT))[\s\n]+)?' +
                                      r'(PENETAPAN|PERATURAN|UNDANG-UNDANG|KEPUTUSAN)[A-Z0-9\W\s\n]+' +
                                      r'((?i:menlhk-setjen|MENHUT|MUT|permentan|per))?[A-Z0-9\W\s\n]+' +
                                      r'(DENGAN\sRAHMAT\sTUHAN\sYANG\sMAHA\sESA)?[A-Z0-9\W\s\n]+(,?))[\s\n]*Menimbang',
                                      texts).group(1)
        else:
            filtered_text = texts
    except Exception:
        try:
            filtered_text = re.search(
                r'(PERUBAHAN[\s\n]+(PERTAMA|KE(DUA|TIGA|]\s+IV))[\s\n]+)?UNDANG[\s\n]*-[\s\n]*UNDANG[\s\n]+DASAR[\s\n]+'
                r'NEGARA[\s\n]+REPUBLIK[\s\n]+INDONESIA[\s\n]+TAHUN[\s\n]+1945', texts).group(1)

        except Exception:
            return ''
    res_funct = {}
    try:
        res_funct = {'type': re.sub(r'[\n\s.]+|PM|NOMOR|PER/', ' ', re.search(r'^([A-Z/,.\-\s\n]+)(PM\.|NOMOR|PER/)',
                                                                        filtered_text).group(1)).strip()}
    except Exception:
        try:
            res_funct = {'type': re.sub(r'[\n\s.]+', ' ', re.search(r'^((PERUBAHAN[\s\n]+(PERTAMA|KE(DUA|TIGA|EMPAT))'
                                                                    r'[\s\n]+)?UNDANG[\s\n]*-[\s\n]*UNDANG[\s\n]+' +
                                                                    r'DASAR[\s\n]+NEGARA[\s\n]+REPUBLIK[\s\n]+' +
                                                                    r'INDONESIA[\s\n]+)TAHUN',
                                                                    filtered_text).group(1).strip())}
        except Exception:
            pass

    try:
        res_funct['number'] = re.sub(r'[\n\s]+', ' ', re.search(r'(NOMOR|PM\.|PER/)[\n\s/]*((:|[A-Za-z]+[\s\n]?[-.]?|' +
                                                                r'[^/\d]+)[\n\s]*)?(\d+)',
                                                                filtered_text).group(4).strip())
    except Exception:
        pass
    try:
        res_funct['year'] = re.sub(r'[\n\s]+', ' ',
                             re.search(r'(TAHUN|/)[\n\s]*(\d{4})(([\s\n]+T[\s\n]*E[\s\n]*N[\s\n]*' +
                                       r'T[\s\n]*A[\s\n]*N[\s\n]*G)?)', filtered_text).group(2).strip())
    except Exception:
        pass
    try:
        res_funct['official'] = re.search(
            r'\n\s*((PJS|PRESIDEN|MENTERI|WALI KOTA|BUPATI|WALIKOTA|GUBERNUR|LEMBAGA|KEPALA|KETUA|DEWAN|BADAN|JAKSA)' +
            r'[A-Z/,\s\n]+),?[\s\n]+$',
            filtered_text).group(1).strip()
    except Exception:
        res_funct['official'] = ''
    try:
        res_funct['name'] = re.sub('DENGAN RAHMAT TUHAN YANG MAHA ESA', '',
                                   re.sub(r'[\n\s]+', ' ',
                                          re.search(r'(T[\s\n]*E[\s\n]*N[\s\n]*T[\s\n]*A[\s\n]*N[\s\n]*G)' +
                                                    r'([\w\W\n\s]+)' + res_funct['official'],
                                                    filtered_text).group(2).strip())).strip()
        res_funct['official'] = re.sub(r'[\n\s]+', ' ', res_funct['official']).strip()
    except Exception:
        pass
    return res_funct

In [5]:
global reg_types

reg_types = pandas.read_csv('regulatory_type.csv')
file_num = 0
state = True
filterDoc = None
result_id = []
file_id = []

while file_num < len(file_list):
    text = file_list[file_num]
    if text == '':
        state = False
    print(file_num, text)
    text = text.strip()
    filesource = text
    dirName = re.sub('/[^/]+$', '', filesource)
    try:
        file = open(filesource, encoding="utf8")
    except Exception:
        file_num += 1
        continue
    res = None
    if re.search('putusan', filesource):
        file_num += 1
        continue
    text = file.read()
    text = re.sub('\n+\s*\d+[^\w;]*([Nn][Oo]\\.\s*(-?\s*\d+\s*-?\s*)+)?\n+', '\n',
                  re.sub(r'\n+(\s*\d+\s*\n+)?', '\n',
                         re.sub('\\nwww.djpp.(depkumham|kemenkumham).go.id|https://jdih.bandung.go.id/|' +
                                r'www.peraturan.go.id\\n', '\n',
                                re.sub(r'[^a-zA-Z\d\n./:(\-,);]', ' ',
                                       re.sub(r'\n+', '\n',
                                              re.sub(r'\n\s*\n', '\n\n', text)))))).strip()
    if re.match(r'^[\s\n\W]*$', text):
        file_num += 1
        continue
    if re.search('(?i)/[^/]*tln|lmp[^/]*$', filesource):
        file_num += 1
        continue
    try:
        result = {'title': get_title(text)}
        try:
            reg_type = reg_types.loc[reg_types['type'] == result['title']['type'].strip(), 'code'].values[0]
            if reg_type not in ['UUD', 'Amandemen_1_UUD', 'Amandemen_2_UUD', 'Amandemen_3_UUD', 'Amandemen_4_UUD']:
                reg_id = reg_type + '_' + result['title']['year'] + '_' + result['title']['number']
            else:
                reg_id = reg_type + '_' + result['title']['year']
            if filterDoc is not None and reg_id.upper() not in filterDoc:
                file_num += 1
                continue
            if reg_type in ['Amandemen_1_UUD', 'Amandemen_2_UUD', 'Amandemen_3_UUD', 'Amandemen_4_UUD']:
                result['title']['change'] = 'UUD_1945'
                result['title']['change_num'] = re.sub(r'[^\d]+', '', reg_type)
            result['title']['reg_id'] = reg_id
            result_id.append(reg_id)
            file_id.append(filesource)
        except:
            continue
    finally: 
        file_num += 1

0 new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_1_tahun_1994_11e4f455eafd9d9e96f8303831303537.txt
1 new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_13_tahun_1994_11e4f455ce0fe070b477303831303039.txt
2 new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_5_tahun_1994_11e4f455bc59cfd09767303830393339.txt
3 new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_11_tahun_1994_11e4f455e25cf3ec9c34303831303433.txt
4 new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_4_tahun_1994_11e4f455c5bbe504856d303830393535.txt
5 new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_6_tahun_1994_11e4f455b2fb1fb69ab7303830393234.txt
6 new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_7_tahun_1994_11e4f455aade1374a598303830393130.txt
7 new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_8_tahun_1994_11e4f4559f0d8066b1aa303830383530.txt
8 new_1_text_files/perda/1994/perda_kabupaten_bantul_nomor_12_tahun_1994_11e4f455d91c1268a69d303831303237.txt
9 new_1_text_fil

84 new_1_text_files/perda/2010/perda_surabaya_nomor_9_tahun_2010_11e577906907d142a964303830393432.txt
85 new_1_text_files/perda/2010/perda_kota_bandung_nomor_9_tahun_2010_11e5778ee142ac108f7b303735383435.txt
86 new_1_text_files/perda/2010/perda_kabupaten_indragiri_hilir_nomor_33_tahun_2010_11e577098ee7f4e69b3f313630343234.txt
87 new_1_text_files/perda/2010/perda_kabupaten_magelang_nomor_14_tahun_2010_11e452bd9dc92da09b44313634353037.txt
88 new_1_text_files/perda/2010/perda_kabupaten_majalengka_nomor_7_tahun_2010_11e577cb076424468f5c313530393139.txt
89 new_1_text_files/perda/2010/perda_kabupaten_magelang_nomor_11_tahun_2010_11e452bd9c194dd082a1313634353034.txt
90 new_1_text_files/perda/2010/perda_kabupaten_purworejo_nomor_5_tahun_2010_11e452bd97cce1e0a1ed313634343537.txt
91 new_1_text_files/perda/2010/perda_kabupaten_hulu_sungai_utara_nomor_10_tahun_2010_11e5770d50da265cb7d7313633313137.txt
92 new_1_text_files/perda/2010/perda_provinsi_jawa_barat_nomor_8_tahun_2010_11e452bd9a5449d0aab63

213 new_1_text_files/perda/2010/perda_kabupaten_ogan_kemiring_ilir_nomor_21_tahun_2010_11e598c1b1cc10129ebd313335353338.txt
214 new_1_text_files/perda/2010/perda_provinsi_jambi_nomor_8_tahun_2010_11e452bd9a49a0909470313634353031.txt
215 new_1_text_files/perda/2010/perda_provinsi_jawa_barat_nomor_12_tahun_2010_11e452bd9d307de0c08c313634353036.txt
216 new_1_text_files/perda/2010/perda_kabupaten_bojonegoro_nomor_8_tahun_2010_11e577940fe6d866a145303833353531.txt
217 new_1_text_files/perda/2010/perda_provinsi_jawa_tengah_nomor_8_tahun_2010_11e452bd9a61f110a5d4313634353031.txt
218 new_1_text_files/perda/2010/perda_kabupaten_indragiri_hilir_nomor_44_tahun_2010_11e57708c2173666b9bf313535383430.txt
219 new_1_text_files/perda/2010/perda_kabupaten_jembrana_nomor_9_tahun_2010_11e539a4efffeb50a592313330303236.txt
220 new_1_text_files/perda/2010/perda_provinsi_kepulauan_riau_nomor_9_tahun_2010_11e452bd9abeed309c37313634353032.txt
221 new_1_text_files/perda/2010/perda_kota_pontianak_nomor_15_tahun_20

290 new_1_text_files/perda/2010/perda_samarinda_nomor_8_tahun_2010_11e577c64684cee6afba313433353137.txt
291 new_1_text_files/perda/2010/perda_kota_pasuruan_nomor_22_tahun_2010_tahun_2010_11e6c827afbc3ad086d1313631393035.txt
292 new_1_text_files/perda/2010/perda_provinsi_sumatera_barat_nomor_6_tahun_2010_11e452bd9931e4609e62313634343539.txt
293 new_1_text_files/perda/2010/perda_kabupaten_probolinggo_nomor_9_tahun_2010_11e5778cb76bac048dae303734333136.txt
294 new_1_text_files/perda/2010/perda_kabupaten_magelang_nomor_4_tahun_2010_11e452bd969629d0a59c313634343535.txt
295 new_1_text_files/perda/2010/perda_kabupaten_sigi_nomor_7_tahun_2010_11e577cc216eb97cb383313531373132.txt
296 new_1_text_files/perda/2010/perda_kabupaten_indragiri_hilir_nomor_16_tahun_2010_11e5770b35e65246c070313631363133.txt
297 new_1_text_files/perda/2010/perda_provinsi_jawa_barat_nomor_9_tahun_2010_11e452bd9ab9bbb08975313634353032.txt
298 new_1_text_files/perda/2010/perda_kabupaten_sigi_nomor_9_tahun_2010_11e5778cfb347

439 new_1_text_files/perda/2010/perda_provinsi_sumatera_selatan_nomor_16_tahun_2010_11e452bd9e71c740a27a313634353038.txt
440 new_1_text_files/perda/2010/perda_kabupaten_karanganyar_nomor_7_tahun_2010_11e577c894745d36a9e7313435313437.txt
441 new_1_text_files/perda/2010/perda_kota_sungai_penuh_nomor_9_tahun_2010_11e576ea74738c7a9909313232313435.txt
442 new_1_text_files/perda/2010/perda_kabupaten_sinjai_nomor_7_tahun_2010_11e577cc3911efaeab12313531373531.txt
443 new_1_text_files/perda/2010/perda_kota_sungai_penuh_nomor_8_tahun_2010_11e577c5464cdb7cb765313432383037.txt
444 new_1_text_files/perda/2010/perda_kota_cirebon_nomor_1_tahun_2010_11e452bd8e5cb7e08fbc313634343431.txt
445 new_1_text_files/perda/2010/perda_kabupaten_jembrana_nomor_8_tahun_2010_11e577946d0ffa9abf60303833383237.txt
446 new_1_text_files/perda/2010/perda_provinsi_kalimantan_tengah_nomor_2_tahun_2010_11e452bd923fc7b0a27b313634343438.txt
447 new_1_text_files/perda/2010/perda_kabupaten_bantul_nomor_nomor2_tahun_2010_tahun_20

...

29512 new_1_text_files/ln/1980/pp21-1980.txt
29513 new_1_text_files/ln/1980/uu1-1980.txt
29514 new_1_text_files/ln/1980/pp3-1980.txt
29515 new_1_text_files/ln/1980/pp41-1980.txt
29516 new_1_text_files/ln/1980/pp53-1980.txt
29517 new_1_text_files/ln/1980/uu11-1980.txt
29518 new_1_text_files/ln/1980/pp55-1980.txt
29519 new_1_text_files/ln/1980/pp54-1980.txt
29520 new_1_text_files/ln/1980/pp11-1980.txt
29521 new_1_text_files/ln/1980/pp16-1980.txt
29522 new_1_text_files/ln/1980/pp13-1980.txt
29523 new_1_text_files/ln/1980/pp22-1980.txt
29524 new_1_text_files/ln/1980/pp30-1980.txt
29525 new_1_text_files/ln/1993/uu0031993.txt
29526 new_1_text_files/ln/1993/uu0041993.txt
29527 new_1_text_files/ln/1993/uu0061993.txt
29528 new_1_text_files/ln/1993/uu0051993.txt
29529 new_1_text_files/ln/1993/uu0071993.txt
29530 new_1_text_files/ln/1993/uu0011993.txt
29531 new_1_text_files/ln/1993/uu0021993.txt
29532 new_1_text_files/ln/2017/ojk9-2017bt.txt
29533 new_1_text_files/ln/2017/ps62-2017.txt
29534 new_

29760 new_1_text_files/ln/2017/pp52-2017bt.txt
29761 new_1_text_files/ln/2017/pp65-2017.txt
29762 new_1_text_files/ln/2017/ps18-2017.txt
29763 new_1_text_files/ln/2017/ojk18-2017bt.txt
29764 new_1_text_files/ln/2017/pbi19-10-2017bt.txt
29765 new_1_text_files/ln/2017/ps84-2017.txt
29766 new_1_text_files/ln/2017/ps85-2017.txt
29767 new_1_text_files/ln/2017/ps55-2017.txt
29768 new_1_text_files/ln/2017/pp2-2017bt.txt
29769 new_1_text_files/ln/2017/ojk51-2017bt.txt
29770 new_1_text_files/ln/2017/pbi19-15-2017bt.txt
29771 new_1_text_files/ln/2017/ps64-2017.txt
29772 new_1_text_files/ln/2017/ojk34-2017bt.txt
29773 new_1_text_files/ln/2017/ps119-2017.txt
29774 new_1_text_files/ln/2017/ps78-2017.txt
29775 new_1_text_files/ln/2017/ojk75-2017bt.txt
29776 new_1_text_files/ln/2017/ps38-2017.txt
29777 new_1_text_files/ln/2017/pp5-2017bt.txt
29778 new_1_text_files/ln/2017/ojk74-2017bt.txt
29779 new_1_text_files/ln/2017/ps40-2017.txt
29780 new_1_text_files/ln/2017/pp21-2017bt.txt
29781 new_1_text_file

29964 new_1_text_files/ln/2016/ps29-2016.txt
29965 new_1_text_files/ln/2016/ojk54-2016bt.txt
29966 new_1_text_files/ln/2016/ojk14-2016bt.txt
29967 new_1_text_files/ln/2016/ojk11-2016bt.txt
29968 new_1_text_files/ln/2016/ps7-2016.txt
29969 new_1_text_files/ln/2016/pp14-2016bt.txt
29970 new_1_text_files/ln/2016/pp19-2016bt.txt
29971 new_1_text_files/ln/2016/bpk2-2016.txt
29972 new_1_text_files/ln/2016/ps37-2016.txt
29973 new_1_text_files/ln/2016/ps115-2016.txt
29974 new_1_text_files/ln/2016/ojk17-2016bt.txt
29975 new_1_text_files/ln/2016/ojk42-2016bt.txt
29976 new_1_text_files/ln/2016/pp75-2016.txt
29977 new_1_text_files/ln/2016/uu12-2016bt.txt
29978 new_1_text_files/ln/2016/ps6-2016.txt
29979 new_1_text_files/ln/2016/ps104-2016.txt
29980 new_1_text_files/ln/2016/pp53-2016.txt
29981 new_1_text_files/ln/2016/ps106-2016.txt
29982 new_1_text_files/ln/2016/ps23-2016.txt
29983 new_1_text_files/ln/2016/pp45-2016bt.txt
29984 new_1_text_files/ln/2016/ps10-2016.txt
29985 new_1_text_files/ln/2016/

30160 new_1_text_files/ln/2016/pbi18-7-2016bt.txt
30161 new_1_text_files/ln/2016/pbi18-8-2016bt.txt
30162 new_1_text_files/ln/2016/ps34-2016.txt
30163 new_1_text_files/ln/2016/pbi18-28-2016.txt
30164 new_1_text_files/ln/2016/ps74-2016.txt
30165 new_1_text_files/ln/2016/ojk33-2016bt.txt
30166 new_1_text_files/ln/2016/pp6-2016bt.txt
30167 new_1_text_files/ln/2016/ojk18-2016bt.txt
30168 new_1_text_files/ln/2016/pp11-2016bt.txt
30169 new_1_text_files/ln/2016/ps16-2016.txt
30170 new_1_text_files/ln/2016/ps77-2016.txt
30171 new_1_text_files/ln/2016/pbi18-1-2016.txt
30172 new_1_text_files/ln/2016/ps2-2016.txt
30173 new_1_text_files/ln/2016/ps3-2016.txt
30174 new_1_text_files/ln/2016/ps28-2016.txt
30175 new_1_text_files/ln/2016/pp33-2016.txt
30176 new_1_text_files/ln/2016/pp98-2016.txt
30177 new_1_text_files/ln/2016/pp62-2016.txt
30178 new_1_text_files/ln/2016/pp35-2016bt.txt
30179 new_1_text_files/ln/2016/ps21-2016.txt
30180 new_1_text_files/ln/2016/ps51-2016.txt
30181 new_1_text_files/ln/201

30377 new_1_text_files/ln/2005/ps29-2005.txt
30378 new_1_text_files/ln/2005/pp66-2005.txt
30379 new_1_text_files/ln/2005/pp62-2005.txt
30380 new_1_text_files/ln/2005/perpu2-2005.txt
30381 new_1_text_files/ln/2005/ps21-2005.txt
30382 new_1_text_files/ln/2005/uu9-2005.txt
30383 new_1_text_files/ln/2005/ps25-2005.txt
30384 new_1_text_files/ln/2005/pp28-2005.txt
30385 new_1_text_files/ln/2005/pp59-2005.txt
30386 new_1_text_files/ln/2005/ps18-2005.txt
30387 new_1_text_files/ln/2005/pp56-2005.txt
30388 new_1_text_files/ln/2005/ps42-2005.txt
30389 new_1_text_files/ln/2005/ps7-2005.txt
30390 new_1_text_files/ln/2005/ps37-2005.txt
30391 new_1_text_files/ln/2005/ps2-2005.txt
30392 new_1_text_files/ln/2005/ps81-2005.txt
30393 new_1_text_files/ln/2005/ps6-2005.txt
30394 new_1_text_files/ln/2005/ps33-2005.txt
30395 new_1_text_files/ln/2005/pp63-2005.txt
30396 new_1_text_files/ln/2005/ps1-2005.txt
30397 new_1_text_files/ln/2005/pp11-2005.txt
30398 new_1_text_files/ln/2005/ps76-2005.txt
30399 new_1_t

In [16]:
import pandas as pd

list_of_tuples = list(zip(result_id, file_id))
list_of_columns = ['regulatory', 'file_txt']

df = pd.DataFrame(list_of_tuples, columns=list_of_columns)
df.to_csv('core/regulatory_list.csv', index=False)

In [7]:
len(set(file_id))

28512

In [8]:
len(set(result_id))

27823

In [9]:
def find_duplicates(lst):
    seen = set()
    duplicates = set()
    
    for item in lst:
        if item in seen:
            duplicates.add(item)
        else:
            seen.add(item)
    
    return list(duplicates)

duplicates = find_duplicates(result_id)
print("Duplicate elements:", duplicates)

Duplicate elements: ['Permen_Humham_2011_05', 'UU_1954_19', 'Permen_Hut_2010_9', 'Perkot_Surabaya_2012_10', 'Perkab_Simeulue_2012_29', 'Perkab_Siak_2013_2', 'Perkab_Mamuju_Utara_2005_13', 'Perkot_Tasikmalaya_2005_6', 'Perkot_Surabaya_2010_9', 'Permen_Ristekdikti_2016_100', 'Perkab_Bantul_2008_13', 'Perkot_Tasikmalaya_2005_5', 'Permen_Keu_2012_21', 'Peraturan_BI_2014_16', 'Perkab_Madiun_2011_6', 'Permen_Hut_2009_35', 'PP_1994_1', 'UU_1984_5', 'Perkab_Bantul_2001_31', 'Perkot_Bandung_2009_09', 'Perkot_Pangkalpinang_2005_09', 'Perprov_Kaltim_2006_02', 'Perprov_Aceh_2008_11', 'Perkab_Gunungkidul_2013_7', 'Perkab_Karawang_2014_13', 'UU_1983_4', 'Perkot_Semarang_2003_4', 'Perkab_Bantul_2007_17', 'Perkab_Magelang_2009_7', 'UU_1997_12', 'Perkot_Semarang_2007_7', 'UU_1990_8', 'UU_1964_1', 'PP_1970_6', 'Permen_Han_2014_42', 'Perkab_Simeulue_2012_26', 'Permen_Humham_2011_01', 'Permen_Hut_2009_4', 'Perkot_Semarang_2006_9', 'Perkab_Pontianak_2010_8', 'Perkot_Kupang_2001_8', 'Perkab_Purwakarta_2013_

# Mapping Regulatory to Files (Turtle & Txt & Json)

In [10]:
import pandas as pd

turtle = pd.read_csv('turtle_map.csv')
text = pd.read_csv('core/regulatory_list.csv')

turtle['regulatory'] = turtle['regulatory'].str.lower()
text['regulatory'] = text['regulatory'].str.lower()

merged_df = pd.merge(turtle, text, on='regulatory', how='left')

pattern = r'^(?!C:/Users/ningg/PycharmProjects/Lexid/data)'
merged_df['ttl_file'] = merged_df['ttl_file'].str.replace(pattern, 'turtle_files/', regex=True)
merged_df['ttl_file'] = merged_df['ttl_file'].str.replace('C:/Users/ningg/PycharmProjects/Lexid/data', 'turtle_files')
merged_df['file_json'] = merged_df['file_txt'].str.replace('new_1_text_files', 'new_parsed_files')
merged_df['file_json'] = merged_df['file_json'].str.replace('.txt', '.json', regex=False)

merged_df

regulatory                               ttl_file  \
0      amandemen_1_uud_1945    turtle_files/bn/2015/bn270-2015.ttl   
1      amandemen_2_uud_1945    turtle_files/bn/2015/bn270-2015.ttl   
2      amandemen_3_uud_1945    turtle_files/bn/2015/bn270-2015.ttl   
3      amandemen_4_uud_1945    turtle_files/bn/2015/bn270-2015.ttl   
4      kepmen_hut_2002_8171     turtle_files/bn/2008/bn29-2008.ttl   
...                     ...                                    ...   
25611             uu_2019_4  turtle_files/bn/2019/bn_1235-2019.ttl   
25612             uu_2019_5    turtle_files/ln/2019/pp8-2019bt.ttl   
25613             uu_2019_7    turtle_files/bn/2019/bn662-2019.ttl   
25614             uu_2019_8   turtle_files/bn/2019/bn_567-2019.ttl   
25615             uu_2019_9    turtle_files/bn/2019/bn639-2019.ttl   

                                                file_txt  \
0      new_1_text_files/lain-lain/1945/uud1945perubah...   
1      new_1_text_files/lain-lain/1945/uud1945perubah...   
2      new_1_text_files/lain-lain/1945/uud1945perubah...   
3      new_1_text_files/lain-lain/1945/uud1945perubah...   
4                 new_1_text_files/bn/2008/bn23-2008.txt   
...                                                  ...   
25611            new_1_text_files/ln/2019/uu4-2019bt.txt   
25612            new_1_text_files/ln/2019/uu5-2019bt.txt   
25613            new_1_text_files/ln/2019/uu7-2019bt.txt   
25614            new_1_text_files/ln/2019/uu8-2019bt.txt   
25615            new_1_text_files/ln/2019/uu9-2019bt.txt   

                                               file_json  
0      new_parsed_files/lain-lain/1945/uud1945perubah...  
1      new_parsed_files/lain-lain/1945/uud1945perubah...  
2      new_parsed_files/lain-lain/1945/uud1945perubah...  
3      new_parsed_files/lain-lain/1945/uud1945perubah...  
4                new_parsed_files/bn/2008/bn23-2008.json  
...                                                  ...  
25611           new_parsed_files/ln/2019/uu4-2019bt.json  
25612           new_parsed_files/ln/2019/uu5-2019bt.json  
25613           new_parsed_files/ln/2019/uu7-2019bt.json  
25614           new_parsed_files/ln/2019/uu8-2019bt.json  
25615           new_parsed_files/ln/2019/uu9-2019bt.json  

[25616 rows x 4 columns]

In [23]:
# df_cleaned = merged_df.dropna(subset=['file_json'])
# # df_cleaned = df_cleaned.drop_duplicates(subset='regulatory', keep=False)
# df_cleaned

regulatory                               ttl_file  \
0      amandemen_1_uud_1945    turtle_files/bn/2015/bn270-2015.ttl   
1      amandemen_2_uud_1945    turtle_files/bn/2015/bn270-2015.ttl   
2      amandemen_3_uud_1945    turtle_files/bn/2015/bn270-2015.ttl   
3      amandemen_4_uud_1945    turtle_files/bn/2015/bn270-2015.ttl   
4      kepmen_hut_2002_8171     turtle_files/bn/2008/bn29-2008.ttl   
...                     ...                                    ...   
25611             uu_2019_4  turtle_files/bn/2019/bn_1235-2019.ttl   
25612             uu_2019_5    turtle_files/ln/2019/pp8-2019bt.ttl   
25613             uu_2019_7    turtle_files/bn/2019/bn662-2019.ttl   
25614             uu_2019_8   turtle_files/bn/2019/bn_567-2019.ttl   
25615             uu_2019_9    turtle_files/bn/2019/bn639-2019.ttl   

                                                file_txt  \
0      new_1_text_files/lain-lain/1945/uud1945perubah...   
1      new_1_text_files/lain-lain/1945/uud1945perubah...   
2      new_1_text_files/lain-lain/1945/uud1945perubah...   
3      new_1_text_files/lain-lain/1945/uud1945perubah...   
4                 new_1_text_files/bn/2008/bn23-2008.txt   
...                                                  ...   
25611            new_1_text_files/ln/2019/uu4-2019bt.txt   
25612            new_1_text_files/ln/2019/uu5-2019bt.txt   
25613            new_1_text_files/ln/2019/uu7-2019bt.txt   
25614            new_1_text_files/ln/2019/uu8-2019bt.txt   
25615            new_1_text_files/ln/2019/uu9-2019bt.txt   

                                               file_json  
0      new_parsed_files/lain-lain/1945/uud1945perubah...  
1      new_parsed_files/lain-lain/1945/uud1945perubah...  
2      new_parsed_files/lain-lain/1945/uud1945perubah...  
3      new_parsed_files/lain-lain/1945/uud1945perubah...  
4                new_parsed_files/bn/2008/bn23-2008.json  
...                                                  ...  
25611           new_parsed_files/ln/2019/uu4-2019bt.json  
25612           new_parsed_files/ln/2019/uu5-2019bt.json  
25613           new_parsed_files/ln/2019/uu7-2019bt.json  
25614           new_parsed_files/ln/2019/uu8-2019bt.json  
25615           new_parsed_files/ln/2019/uu9-2019bt.json  

[25453 rows x 4 columns]

In [29]:
df_cleaned['file_json'].nunique()

25453

In [30]:
df_cleaned['regulatory'].nunique()

24810

In [31]:
duplicates = df_cleaned['regulatory'].value_counts()[lambda x: x > 1].index
filt = df_cleaned[df_cleaned['regulatory'].isin(duplicates)]
filt

regulatory  \
10     pb_ma_menhumham_menkes_mensos_jagung_kapolri_b...   
11     pb_ma_menhumham_menkes_mensos_jagung_kapolri_b...   
43                           perkab_bangka_tengah_2011_2   
44                           perkab_bangka_tengah_2011_2   
49                                  perkab_bantul_2001_4   
...                                                  ...   
24933                                          uu_1990_8   
25004                                         uu_1997_12   
25005                                         uu_1997_12   
25271                                         uu_2005_13   
25272                                         uu_2005_13   

                                                ttl_file  \
10                   turtle_files/ln/2014/ps103-2014.ttl   
11                   turtle_files/ln/2014/ps103-2014.ttl   
43     turtle_files/perda/2011/perda_kabupaten_bangka...   
44     turtle_files/perda/2011/perda_kabupaten_bangka...   
49     turtle_files/perda/2001/perda_kabupaten_solok_...   
...                                                  ...   
24933                 turtle_files/ln/1990/pp14-1990.ttl   
25004                 turtle_files/ln/1997/pp16-1997.ttl   
25005                 turtle_files/ln/1997/pp16-1997.ttl   
25271                 turtle_files/ln/2005/pp18-2005.ttl   
25272                 turtle_files/ln/2005/pp18-2005.ttl   

                                                file_txt  \
10            new_1_text_files/bn/2014/pb_bn465-2014.txt   
11               new_1_text_files/bn/2014/bn465-2014.txt   
43     new_1_text_files/perda/2011/perda_kabupaten_ba...   
44     new_1_text_files/perda/2011/perda_kabupaten_ba...   
49     new_1_text_files/perda/2001/perda_kabupaten_ba...   
...                                                  ...   
24933              new_1_text_files/ln/1990/uu9-1990.txt   
25004             new_1_text_files/ln/1997/uu12-1997.txt   
25005             new_1_text_files/ln/1997/uu11-1997.txt   
25271             new_1_text_files/ln/2006/uu14-2006.txt   
25272             new_1_text_files/ln/2005/uu13-2005.txt   

                                               file_json  
10           new_parsed_files/bn/2014/pb_bn465-2014.json  
11              new_parsed_files/bn/2014/bn465-2014.json  
43     new_parsed_files/perda/2011/perda_kabupaten_ba...  
44     new_parsed_files/perda/2011/perda_kabupaten_ba...  
49     new_parsed_files/perda/2001/perda_kabupaten_ba...  
...                                                  ...  
24933             new_parsed_files/ln/1990/uu9-1990.json  
25004            new_parsed_files/ln/1997/uu12-1997.json  
25005            new_parsed_files/ln/1997/uu11-1997.json  
25271            new_parsed_files/ln/2006/uu14-2006.json  
25272            new_parsed_files/ln/2005/uu13-2005.json  

[1110 rows x 4 columns]

In [32]:
filt['regulatory'].value_counts()

peraturan_bi_2016_18       43
peraturan_bpom_2011_03     25
peraturan_bi_2018_20       16
peraturan_bi_2017_19       14
peraturan_bi_2015_17       13
                           ..
perkab_simeulue_2012_16     2
perkab_simeulue_2012_14     2
perkab_simeulue_2012_12     2
perkab_simeulue_2012_11     2
uu_2005_13                  2
Name: regulatory, Length: 467, dtype: int64

In [17]:
# c = pd.read_csv('turtle_map.csv')

# c = c[c['regulatory'].str.lower().isin(df_cleaned['regulatory'])]
# c

regulatory                                           ttl_file
0      Amandemen_1_UUD_1945                             bn/2015/bn270-2015.ttl
1      Amandemen_2_UUD_1945                             bn/2015/bn270-2015.ttl
2      Amandemen_3_UUD_1945                             bn/2015/bn270-2015.ttl
3      Amandemen_4_UUD_1945                             bn/2015/bn270-2015.ttl
4      Kepmen_Hut_2002_8171  C:/Users/ningg/PycharmProjects/Lexid/data/bn/2...
...                     ...                                                ...
24968             UU_2019_4  C:/Users/ningg/PycharmProjects/Lexid/data/bn/2...
24969             UU_2019_5  C:/Users/ningg/PycharmProjects/Lexid/data/ln/2...
24970             UU_2019_7  C:/Users/ningg/PycharmProjects/Lexid/data/bn/2...
24971             UU_2019_8  C:/Users/ningg/PycharmProjects/Lexid/data/bn/2...
24972             UU_2019_9  C:/Users/ningg/PycharmProjects/Lexid/data/bn/2...

[24810 rows x 2 columns]

In [27]:
c = pd.read_csv('core/turtle_map.csv')

r = df_cleaned[~df_cleaned['regulatory'].str.lower().isin(df_cleaned['regulatory'])]
r

Empty DataFrame
Columns: [regulatory, ttl_file, file_txt, file_json]
Index: []

In [18]:
# d = pd.read_csv('core/turtle_map.csv')
# d = d[~d['ttl_file'].str.contains('ningg')]
# d

regulatory                                           ttl_file
0      Amandemen_1_UUD_1945  new_turtle_fileslain-lain1945uud1945perubahanp...
1      Amandemen_2_UUD_1945  new_turtle_fileslain-lain1945uud1945perubahank...
2      Amandemen_3_UUD_1945  new_turtle_fileslain-lain1945uud1945perubahank...
3      Amandemen_4_UUD_1945  new_turtle_fileslain-lain1945uud1945perubahank...
4      Kepmen_Hut_2002_8171                new_turtle_filesbn2008bn23-2008.ttl
...                     ...                                                ...
24968             UU_2019_4               new_turtle_filesln2019uu4-2019bt.ttl
24969             UU_2019_5               new_turtle_filesln2019uu5-2019bt.ttl
24970             UU_2019_7               new_turtle_filesln2019uu7-2019bt.ttl
24971             UU_2019_8               new_turtle_filesln2019uu8-2019bt.ttl
24972             UU_2019_9               new_turtle_filesln2019uu9-2019bt.ttl

[24811 rows x 2 columns]

In [12]:
import pandas as pd

turtle = pd.read_csv('turtle_map.csv')
text = pd.read_csv('regulatory_list.csv')

turtle['regulatory'] = turtle['regulatory'].str.lower()
text['regulatory'] = text['regulatory'].str.lower()

merged_df = pd.merge(turtle, text, on='regulatory', how='left')

pattern = r'^(?!C:/Users/ningg/PycharmProjects/Lexid/data)'
merged_df['ttl_file'] = merged_df['ttl_file'].str.replace(pattern, 'turtle_files/', regex=True)
merged_df['ttl_file'] = merged_df['ttl_file'].str.replace('C:/Users/ningg/PycharmProjects/Lexid/data', 'turtle_files')
merged_df['file_json'] = merged_df['file_txt'].str.replace('new_1_text_files', 'new_parsed_files')
merged_df['file_json'] = merged_df['file_json'].str.replace('.txt', '.json', regex=False)

merged_df

regulatory                               ttl_file  \
0      amandemen_1_uud_1945    turtle_files/bn/2015/bn270-2015.ttl   
1      amandemen_2_uud_1945    turtle_files/bn/2015/bn270-2015.ttl   
2      amandemen_3_uud_1945    turtle_files/bn/2015/bn270-2015.ttl   
3      amandemen_4_uud_1945    turtle_files/bn/2015/bn270-2015.ttl   
4      kepmen_hut_2002_8171     turtle_files/bn/2008/bn29-2008.ttl   
...                     ...                                    ...   
25611             uu_2019_4  turtle_files/bn/2019/bn_1235-2019.ttl   
25612             uu_2019_5    turtle_files/ln/2019/pp8-2019bt.ttl   
25613             uu_2019_7    turtle_files/bn/2019/bn662-2019.ttl   
25614             uu_2019_8   turtle_files/bn/2019/bn_567-2019.ttl   
25615             uu_2019_9    turtle_files/bn/2019/bn639-2019.ttl   

                                                          file_txt  \
0      new_1_text_files/lain-lain/1945/uud1945perubahanpertama.txt   
1        new_1_text_files/lain-lain/1945/uud1945perubahankedua.txt   
2       new_1_text_files/lain-lain/1945/uud1945perubahanketiga.txt   
3      new_1_text_files/lain-lain/1945/uud1945perubahankeempat.txt   
4                           new_1_text_files/bn/2008/bn23-2008.txt   
...                                                            ...   
25611                      new_1_text_files/ln/2019/uu4-2019bt.txt   
25612                      new_1_text_files/ln/2019/uu5-2019bt.txt   
25613                      new_1_text_files/ln/2019/uu7-2019bt.txt   
25614                      new_1_text_files/ln/2019/uu8-2019bt.txt   
25615                      new_1_text_files/ln/2019/uu9-2019bt.txt   

                                                          file_json  
0      new_parsed_files/lain-lain/1945/uud1945perubahanpertama.json  
1        new_parsed_files/lain-lain/1945/uud1945perubahankedua.json  
2       new_parsed_files/lain-lain/1945/uud1945perubahanketiga.json  
3      new_parsed_files/lain-lain/1945/uud1945perubahankeempat.json  
4                           new_parsed_files/bn/2008/bn23-2008.json  
...                                                             ...  
25611                      new_parsed_files/ln/2019/uu4-2019bt.json  
25612                      new_parsed_files/ln/2019/uu5-2019bt.json  
25613                      new_parsed_files/ln/2019/uu7-2019bt.json  
25614                      new_parsed_files/ln/2019/uu8-2019bt.json  
25615                      new_parsed_files/ln/2019/uu9-2019bt.json  

[25616 rows x 4 columns]

In [17]:
merged_df.to_csv('core/regulatory_map.csv', index=False)

In [20]:
import pandas as pd

tes = pd.read_csv('core/regulatory_map.csv')
tes['file_json'].nunique()

25453

In [21]:
tes['regulatory'].nunique()

24973

# Create New Turtle Folder

In [14]:
root = 'new_turtle_files'
if not os.path.exists(root):
    os.makedirs(root)

for root, dirs, _ in os.walk('new_parsed_files'):
    for directory in dirs:
        f1 = os.path.join(root, directory)
        f2 = f1.replace('new_parsed_files', 'new_turtle_files', 1)
        if not os.path.exists(f2):
            os.makedirs(f2)
        print(f2)

new_turtle_files/perda
new_turtle_files/putusan
new_turtle_files/bn
new_turtle_files/ln
new_turtle_files/lain-lain
new_turtle_files/perda/1994
new_turtle_files/perda/1982
new_turtle_files/perda/1992
new_turtle_files/perda/2015
new_turtle_files/perda/2010
new_turtle_files/perda/2003
new_turtle_files/perda/1979
new_turtle_files/perda/2019
new_turtle_files/perda/2012
new_turtle_files/perda/1998
new_turtle_files/perda/1989
new_turtle_files/perda/1996
new_turtle_files/perda/1976
new_turtle_files/perda/2008
new_turtle_files/perda/2013
new_turtle_files/perda/1984
new_turtle_files/perda/2002
new_turtle_files/perda/1991
new_turtle_files/perda/1995
new_turtle_files/perda/1986
new_turtle_files/perda/1983
new_turtle_files/perda/2006
new_turtle_files/perda/2011
new_turtle_files/perda/2004
new_turtle_files/perda/1977
new_turtle_files/perda/1999
new_turtle_files/perda/2009
new_turtle_files/perda/1985
new_turtle_files/perda/1997
new_turtle_files/perda/1990
new_turtle_files/perda/2014
new_turtle_files/

# Create PDF List

In [23]:
import pandas as pd

merged_df = pd.read_csv('core/regulatory_map.csv')

jsons = merged_df['file_json']

with open('core/pdf_list.txt', 'w') as f:
    for index, json in jsons.items():
        if pd.isna(json):
            continue
        print(json)
        f.write(f'{json}\n')

new_parsed_files/lain-lain/1945/uud1945perubahanpertama.json
new_parsed_files/lain-lain/1945/uud1945perubahankedua.json
new_parsed_files/lain-lain/1945/uud1945perubahanketiga.json
new_parsed_files/lain-lain/1945/uud1945perubahankeempat.json
new_parsed_files/bn/2008/bn23-2008.json
new_parsed_files/bn/2018/bn1069-2018.json
new_parsed_files/ln/1990/kp3-1990.json
new_parsed_files/ln/1992/kp48-1992.json
new_parsed_files/ln/1992/kp5-1992.json
new_parsed_files/bn/2013/bn332-2013.json
new_parsed_files/bn/2014/pb_bn465-2014.json
new_parsed_files/bn/2014/bn465-2014.json
new_parsed_files/bn/2014/bn529-2014.json
new_parsed_files/bn/2009/bn558-2009.json
new_parsed_files/bn/2015/bn1040-2015.json
new_parsed_files/bn/2014/bn308-2014.json
new_parsed_files/bn/2014/bn1696-2014.json
new_parsed_files/bn/2015/bn960-2015.json
new_parsed_files/bn/2012/bn166-2012.json
new_parsed_files/bn/2015/bn678-2015.json
new_parsed_files/bn/2012/bn1283-2012.json
new_parsed_files/bn/2013/bn1441-2013.json
new_parsed_files/bn